In [3]:
import os

def read_data_from_folder(folder_path):
    documents = {}
    for filename in os.listdir(folder_path):
        if filename.endswith(".txt"):
            filepath = os.path.join(folder_path, filename)
            with open(filepath, 'r', encoding='utf-8') as f:
                lines = f.readlines()
                if len(lines) >= 2:
                    url = lines[0].strip()
                    content = " ".join(line.strip() for line in lines[1:])
                    doc_id = filename[:-4]  # bỏ ".txt"
                    documents[doc_id] = {"url": url, "text": content}
    return documents

documents = read_data_from_folder("Corpus_Modified_Zipped")

In [4]:
documents

{'alzheimer': {'url': 'https://tamanhhospital.vn/alzheimer/',
  'text': 'Triệu chứng thường gặp của hội chứng Alzheimer   Bộ não của chúng ta được tạo thành từ hơn 100 tỷ tế bào thần kinh – nhiều hơn cả các ngôi sao trong dải ngân hà. Chứng mất trí nhớ làm tổn thương các tế bào thần kinh khiến chúng không còn khả năng giao tiếp hiệu quả và điều này ảnh hưởng đến cách cơ thể chúng ta hoạt động. Các triệu chứng cụ thể mà một người sống chung với Alzheimer trải qua sẽ phụ thuộc vào những phần nào của não bị ảnh hưởng hoặc căn bệnh cụ thể đang gây ra chứng mất trí của họ. Các triệu chứng có thể bao gồm:   1. Sa sút trí nhớ và khả năng nhận thức   Hầu hết trí nhớ và các khả năng nhận thức khác của mọi người dần trở nên kém đi khi về già. Lúc này cơ thể không còn có thể phản ứng nhanh và linh hoạt với các tình huống, đây được xem là một phần tự nhiên của quá trình lão hóa. Việc nhận ra và giải quyết các vấn đề phát sinh thường khó khăn hơn nhưng họ vẫn có thể tiếp cận với những kiến \u200b\u

In [5]:
from pyvi import ViTokenizer

def preprocess_text(text):
    text = text.lower()
    tokenized = ViTokenizer.tokenize(text)
    return tokenized.split()

# Tiền xử lý từng văn bản
preprocessed_documents = {
    doc_id: {
        "url": data["url"],
        "tokens": preprocess_text(data["text"])
    }
    for doc_id, data in documents.items()
}


In [40]:
import json

# Đường dẫn lưu file
output_path = "preprocessed_documents.json"

# Ghi file
with open(output_path, "w", encoding="utf-8") as f:
    json.dump(preprocessed_documents, f, ensure_ascii=False, indent=2)


In [6]:
from rank_bm25 import BM25Okapi

# Chuẩn bị dữ liệu cho BM25
tokenized_corpus = [data["tokens"] for data in preprocessed_documents.values()]
bm25 = BM25Okapi(tokenized_corpus)

# Danh sách các doc_ids tương ứng với corpus
doc_ids = list(preprocessed_documents.keys())

In [ ]:
def search_symptoms(query, top_k=10):
    tokenized_query = preprocess_text(query)
    scores = bm25.get_scores(tokenized_query)
    top_indexes = sorted(range(len(scores)), key=lambda i: scores[i], reverse=True)[:top_k]
    
    results = []
    for i in top_indexes:
        doc_id = doc_ids[i]
        score = scores[i]
        results.append({
            "doc_id": doc_id,
            "url": preprocessed_documents[doc_id]["url"],
            "score": score,
            "preview": " ".join(preprocessed_documents[doc_id]["tokens"][:50])
        })
    return results

# Ví dụ
query = "sốt cao, mệt mỏi, nổi ban đỏ"
results = search_symptoms(query)
for r in results:
    if r['score'] > 5:
        print(f"- {r['doc_id']} ({r['score']:.2f}): {r['url']}\n   {r['preview']}...\n")

- benh-tay-chan-mieng (20.53): https://tamanhhospital.vn/benh-tay-chan-mieng/
   triệu_chứng_bệnh tay_chân miệng mặc_dù bệnh tay_chân miệng ở trẻ có_thể được gây ra bởi nhiều chủng virus khác nhau , tuy_nhiên các triệu_chứng ban_đầu của bệnh gần như giống nhau , dễ gây nhầm_lẫn với các bệnh khác như : sốt nhẹ , mệt_mỏi , chán ăn . dựa trên...

- benh-dau-mua-khi (17.99): https://tamanhhospital.vn/benh-dau-mua-khi/
   triệu_chứng_bệnh đậu_mùa khỉ các triệu_chứng xuất_hiện đầu_tiên khi một người mắc bệnh đậu_mùa khỉ bao_gồm : sốt ( thường là triệu_chứng_bệnh đầu_tiên ) đau_đầu dữ_dội đau mỏi lưng và các cơ ớn lạnh mệt_mỏi uể_oải nổi hạch sau khi có biểu_hiện sốt , người bị bệnh đậu_mùa khỉ có_thể bị...

- benh-viem-hong-cap (17.59): https://tamanhhospital.vn/benh-viem-hong-cap/
   triệu_chứng viêm họng cấp_tính bác_sĩ hương cho biết , các dấu_hiệu viêm họng cấp thường chỉ kéo_dài từ 1 - 2 tuần . các triệu_chứng chung thường bao_gồm họng sưng , đỏ , ngứa , rát , đau , có_thể ho , khàn giọ

In [ ]:
def search_boolean(query, top_k=10):
    tokenized_query = set(preprocess_text(query))
    results = []

    for doc_id, data in preprocessed_documents.items():
        doc_tokens = set(data["tokens"])
        if tokenized_query & doc_tokens:  # ít nhất 1 token trùng
            results.append({
                "doc_id": doc_id,
                "url": data["url"],
                "preview": " ".join(data["tokens"][:50])
            })
    
    # Trả về top_k
    return results[:top_k]

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.metrics.pairwise import cosine_similarity

# Ghép tokens lại để vector hóa
docs_as_text = [" ".join(data["tokens"]) for data in preprocessed_documents.values()]
vectorizer = TfidfVectorizer()
X_tfidf = vectorizer.fit_transform(docs_as_text)

# LSA với 100
svd = TruncatedSVD(n_components=100, random_state=42)
X_lsa = svd.fit_transform(X_tfidf)

# Lưu lại doc_id theo thứ tự
doc_ids_lsa = list(preprocessed_documents.keys())


In [35]:
def search_lsa(query, top_k=5):
    query_tokens = " ".join(preprocess_text(query))
    query_vec = vectorizer.transform([query_tokens])
    query_lsa = svd.transform(query_vec)

    sims = cosine_similarity(query_lsa, X_lsa)[0]
    top_indexes = sims.argsort()[::-1][:top_k]

    results = []
    for i in top_indexes:
        doc_id = doc_ids_lsa[i]
        results.append({
            "doc_id": doc_id,
            "url": preprocessed_documents[doc_id]["url"],
            "score": sims[i],
            "preview": " ".join(preprocessed_documents[doc_id]["tokens"][:50])
        })
    return results


In [36]:
query = "sốt cao, mệt mỏi, nổi ban đỏ"

# Boolean
boolean_results = search_boolean(query)

# LSA
lsa_results = search_lsa(query)


In [37]:
print("Kết quả tìm kiếm LSA:")
for r in lsa_results:
    print(f"- {r['doc_id']}: {r['url']}\n   {r['preview']}...\n")

Kết quả tìm kiếm LSA:
- benh-tay-chan-mieng: https://tamanhhospital.vn/benh-tay-chan-mieng/
   triệu_chứng_bệnh tay_chân miệng mặc_dù bệnh tay_chân miệng ở trẻ có_thể được gây ra bởi nhiều chủng virus khác nhau , tuy_nhiên các triệu_chứng ban_đầu của bệnh gần như giống nhau , dễ gây nhầm_lẫn với các bệnh khác như : sốt nhẹ , mệt_mỏi , chán ăn . dựa trên...

- hoi-chung-stevens-johnson: https://tamanhhospital.vn/hoi-chung-stevens-johnson/
   triệu_chứng thường gặp hội_chứng stevens johnson có biểu_hiện đặc_trưng là những nốt lở_loét ở các lỗ tự_nhiên của cơ_thể như mắt , mũi , miệng , họng , đường tiểu … đối_với nữ_giới , tình_trạng lở_loét âm_hộ , âm_đạo có_thể xảy ra kèm chảy_máu . còn ở nam_giới , ngoài...

- benh-cham: https://tamanhhospital.vn/benh-cham/
   triệu_chứng_bệnh chàm với mỗi người , biểu_hiện bệnh chàm sẽ khác nhau . các đợt bùng_phát không phải lúc_nào cũng xảy ra trong cùng một khu_vực . triệu_chứng đặc_trưng của bệnh chàm là ngứa , đôi_khi biểu_hiện ngứa xuất_hiện tr